In [2]:
from google.colab import drive
drive.mount('/gdrive')

Mounted at /gdrive


In [3]:
import torch
import numpy as np

if torch.cuda.is_available():
    device = torch.device("cuda")
    print("There are %s GPU's." %torch.cuda.device_count())
    print("GPU Name: " , torch.cuda.get_device_name(0))

else:
    print("No GPU's Available :(")
    decive = torch.device("cpu")

There are 1 GPU's.
GPU Name:  Tesla T4


In [5]:
# !pip install transformers
import transformers

In [6]:
#configurations
MAX_LEN = 512
TRAIN_BATCH_SIZE = 4
VALIDATION_BATCH_SIZE = 4
EPOCHS = 10
ACCUMULATION = 2
BERT_PATH = "/gdrive/MyDrive/bert_base_uncased/"
MODEL_PATH = "/gdrive/MyDrive/bert_base_uncased/"
TRAINING_FILE = "/gdrive/MyDrive/bert_base_uncased/IMDB Dataset.csv"
TOKENIZER = transformers.BertTokenizer.from_pretrained(
    BERT_PATH, 
    do_lower_case = True
)

In [7]:
#data_loader

#https://pytorch.org/tutorials/beginner/basics/data_tutorial.html
class BERTDataset:
    def __init__(self , sentence , target):
        """
            sentence : list of strings(sentences)
            target : list of ints
        """
        self.sentence = sentence
        self.target = target
        self.tokenizer = TOKENIZER
        self.max_len = MAX_LEN

    #total len of dataset
    def __len__(self):
        return len(self.sentence)

    def __getitem__(self , idx):
        sentence = str(self.sentence[idx])   #just to make sure everything is string and not ints or UTF
        sentence = " ".join(sentence.split())

        #tokeizing the sentences
        inputs = self.tokenizer.encode_plus(
            text = sentence,
            add_special_tokens = True,
            max_length = self.max_len,
            padding='max_length',
            truncation = True
            # return_attention_mask = True
        )

        ids = inputs["input_ids"]
        mask = inputs["attention_mask"]
        # print(f"inputs {len(ids) } , mask {len(mask)}  len {len(sentence.split())}  target {self.target[idx]}")

        return {
            'ids' : torch.tensor(ids  , dtype = torch.long),
            'mask' : torch.tensor(mask , dtype = torch.long),
            'targets' : torch.tensor(self.target[idx] , dtype = torch.float)
        }

        


In [8]:
#model
# import transformers
import torch.nn as nn

class BERTBaseUncased(nn.Module):
    def __init__(self):
        super(BERTBaseUncased, self).__init__()
        self.bert = transformers.BertModel.from_pretrained(BERT_PATH)
        self.bert_drop = nn.Dropout(p = 0.3)
        self.out = nn.Linear(768 , 1)   #change 1 to number of intnents and also add actication functions

    def forward(self, ids , mask):
        #out1 = (batch_size, sequence_length, 786) – Sequence of hidden-states at the output of the last layer of the model.
        #out2 = (batch_size, 786) – Last layer hidden-state of the first token of the sequence (classification token) (?? not sure what this is)
        #                         – Gives a vector of size 768 for each sample in batch
        #https://huggingface.co/transformers/model_doc/bert.html#bertmodel
        _ , out2 = self.bert(
            input_ids = ids,
            attention_mask = mask,
            return_dict=False
            # token_type_ids = token_type_ids     #not sure if it's necessary for this task
        )

        bert_output = self.bert_drop(out2)
        output = self.out(bert_output)
        return output 



    


In [9]:
#engine
# !pip install tqdm 
from tqdm import tqdm

def loss_fn(outputs , targets):
    return nn.BCEWithLogitsLoss()(outputs , targets.view(-1,1))

def train_fn(data_loader , model , optimizer , device , accumulation_steps,schedular):
    model.train()

    #loop through each batch
    for batch_index , data_batch in tqdm(enumerate(data_loader) , total = len(data_loader)):
        ids = data_batch["ids"]
        mask =  data_batch["mask"]
        targets = data_batch["targets"]

        ids = ids.to(device, dtype = torch.long)
        mask = mask.to(device, dtype = torch.long)
        targets = targets.to(device, dtype = torch.float)

        optimizer.zero_grad()
        outputs = model(
            ids = ids,
            mask = mask
        )

        # print(f"inputs {len(ids) } , mask {len(mask)}  target {targets.shape}")
        loss = loss_fn(outputs, targets)
        loss.backward()
        print(f"loss = {loss.item()}")
        # optimizer.step()
        # schedular.step()     

        if (batch_index + 1) % accumulation_steps == 0:
            optimizer.step()
            schedular.step()


def eval_fn(data_loader , model, device):
    model.eval()
    final_targets = []
    final_outputs = []

    #loop through each batch
    with torch.no_grad():   #??
        for batch_index , data_batch in tqdm(enumerate(data_loader) , total = len(data_loader)):
            ids = data_batch['ids']
            mask =  data_batch['mask']
            targets = data_batch['targets']

            ids = ids.to(device, dtype = torch.long)
            mask = mask.to(device, dtype = torch.long)
            targets = targets.to(device, dtype = torch.float)

            outputs = model(
                ids = ids,
                mask = mask
            )

            final_targets.extend(targets.cpu().detach().numpy().tolist())
            final_outputs.extend(torch.sigmoid(outputs).cpu().detach().numpy().tolist())    #change this in case of multiple outputs

    return final_outputs , final_targets


In [ ]:
#train
import pandas as pd
from sklearn import model_selection
from sklearn import metrics
from transformers import AdamW
from transformers import get_linear_schedule_with_warmup

def run():
    df = pd.read_csv(TRAINING_FILE).fillna("none")
    print(df.head())

    #change this lambda mapping in multiple intent classification
    df.sentiment = df.sentiment.apply(
        lambda x : 1 if x == 'positive' else 0
    )


    df_train, df_valid = model_selection.train_test_split(
        df,
        test_size = 0.1,
        random_state = 2000,
        stratify = df.sentiment.values
    )

    df_train = df_train.reset_index(drop = True)
    df_valid = df_valid.reset_index(drop = True)

    train_dataset = BERTDataset(
        sentence = df_train.review.values , 
        target = df_train.sentiment.values
    )

    valid_dataset = BERTDataset(
        sentence = df_valid.review.values , 
        target = df_valid.sentiment.values
    )

    train_data_loader = torch.utils.data.DataLoader(
        train_dataset ,
        batch_size = TRAIN_BATCH_SIZE, 
        num_workers = 1
    )

    valid_data_loader = torch.utils.data.DataLoader(
        valid_dataset ,
        batch_size = VALIDATION_BATCH_SIZE, 
        num_workers = 1
    )

    model = BERTBaseUncased()
    model.to(device)
    params = (list(model.named_parameters()))
    for p in params:
        print("{:<55} {:>12}".format(p[0], str(tuple(p[1].size()))))

    param_optimizer = list(model.named_parameters())
    no_decay = ["bias", "LayerNorm.bias", "LayerNorm.weight"]
 
    optimizer_parameters = [
        {
            "params": [
                p for n, p in param_optimizer if not any(nd in n for nd in no_decay)
            ],
            "weight_decay": 0.001,
        },
        {
            "params": [
                p for n, p in param_optimizer if any(nd in n for nd in no_decay)
            ],
            "weight_decay": 0.0,
        },
    ]   

    num_train_steps = len(df_train)/TRAIN_BATCH_SIZE * EPOCHS
    optimizer = AdamW(
        optimizer_parameters,
        lr = 2e-5
    )
    scheduler = get_linear_schedule_with_warmup(
        optimizer, num_warmup_steps=0, num_training_steps=num_train_steps
    )

    best_accuracy = 0
    for epoch in range(EPOCHS):
        train_fn(train_data_loader , model , optimizer , device , ACCUMULATION , scheduler)

        outputs , targets = eval_fn(valid_data_loader , model, device )
        outputs = np.array(outputs) >= 0.5
        accuracy = metrics.accuracy_score(targets , outputs)
        print(f"Accuracy Score = {accuracy}")

run()



                                              review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive


Some weights of the model checkpoint at /gdrive/MyDrive/bert_base_uncased/ were not used when initializing BertModel: ['cls.predictions.transform.dense.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


bert.embeddings.word_embeddings.weight                  (30522, 768)
bert.embeddings.position_embeddings.weight                (512, 768)
bert.embeddings.token_type_embeddings.weight                (2, 768)
bert.embeddings.LayerNorm.weight                              (768,)
bert.embeddings.LayerNorm.bias                                (768,)
bert.encoder.layer.0.attention.self.query.weight          (768, 768)
bert.encoder.layer.0.attention.self.query.bias                (768,)
bert.encoder.layer.0.attention.self.key.weight            (768, 768)
bert.encoder.layer.0.attention.self.key.bias                  (768,)
bert.encoder.layer.0.attention.self.value.weight          (768, 768)
bert.encoder.layer.0.attention.self.value.bias                (768,)
bert.encoder.layer.0.attention.output.dense.weight        (768, 768)
bert.encoder.layer.0.attention.output.dense.bias              (768,)
bert.encoder.layer.0.attention.output.LayerNorm.weight        (768,)
bert.encoder.layer.0.attention.out

  0%|          | 1/11250 [00:00<1:48:34,  1.73it/s]

loss = 0.6706038117408752


...

loss = 0.05290408059954643


 17%|█▋        | 1958/11250 [14:18<1:08:25,  2.26it/s]

loss = 0.030737150460481644


 17%|█▋        | 1959/11250 [14:19<1:07:15,  2.30it/s]

loss = 0.030868783593177795
